In [9]:
import sys

import pandas as pd
import sqlite3
# from datadings.tools import yield_threaded
from tqdm import tqdm

from Harmony.models import Harmony

# from Harmony.models.clip import CLIP_VITL16
# from Harmony.models.dinov2 import vit_large
import argparse

from Harmony import utils
import Harmony.vision_transformer as vits

import torch
import torchvision

In [2]:
args = argparse.Namespace(arch='vit_small', batch_size_per_gpu=1, clip_grad=3.0, data='CC3M:/mnt/d/data/CC3M/cc3m/', dist_url='env://', drop_path_rate=0.1, epochs=100, freeze_last_layer=1, global_crops_scale=(0.4, 1.0), gpu=0, local_crops_number=8, local_crops_scale=(0.05, 0.4), local_rank=0, lr=0.0005, min_lr=1e-06, momentum_teacher=0.996, norm_last_layer=True, num_workers=10, objective='dino', optimizer='adamw', out_dim=65536, output_dir='/mnt/c/Users/Moham/Desktop/KAUST/results', patch_size=16, rank=0, saveckp_freq=20, seed=0, teacher_temp=0.04, use_bn_in_head=False, use_fp16=True, warmup_epochs=10, warmup_teacher_temp=0.04, warmup_teacher_temp_epochs=0, weight_decay=0.04, weight_decay_end=0.4, world_size=1)

In [4]:
checkpoint = torch.load(r"/mnt/c/Users/Moham/Desktop/KAUST/results/checkpoint0000.pth", map_location="cpu")

In [6]:
# utils.init_distributed_mode(args)
# utils.fix_random_seeds(args.seed)

# model = Harmony(args=args)

model = vits.__dict__[args.arch](patch_size=args.patch_size, num_classes=0)

In [8]:
print(len(checkpoint['main_vit'].keys()))

150


In [7]:
checkpoint_key = "main_vit"
state_dict = torch.load(r"/mnt/c/Users/Moham/Desktop/KAUST/results/checkpoint0000.pth", map_location="cpu")

if checkpoint_key is not None and checkpoint_key in state_dict:
    print(f"Take key {checkpoint_key} in provided checkpoint dict")
    state_dict = state_dict[checkpoint_key]
# remove `module.` prefix
# state_dict = {k.replace("module.", ""): v for k, v in state_dict.items()}
# # remove `backbone.` prefix induced by multicrop wrapper
# state_dict = {k.replace("backbone.", ""): v for k, v in state_dict.items()}
msg = model.load_state_dict(state_dict, strict=False)

Take key main_vit in provided checkpoint dict


In [8]:
msg

<All keys matched successfully>

In [39]:
msg

_IncompatibleKeys(missing_keys=[], unexpected_keys=['head.mlp.0.weight', 'head.mlp.0.bias', 'head.mlp.2.weight', 'head.mlp.2.bias', 'head.mlp.4.weight', 'head.mlp.4.bias', 'head.last_layer.weight_g', 'head.last_layer.weight_v'])

In [44]:
print([i for i in model.parameters()])

[Parameter containing:
tensor([[[-1.2056e-02,  1.3396e-02, -9.5379e-04, -1.7326e-03,  6.0872e-03,
           5.1733e-03,  2.0648e-02, -2.9618e-02, -1.3020e-02, -4.3593e-04,
           2.0244e-02, -2.3509e-02,  1.9101e-02,  7.5702e-03,  2.7332e-03,
          -5.6657e-04, -1.2750e-02,  1.6867e-02, -1.2027e-02, -1.2219e-02,
           1.8671e-02, -9.5714e-03,  1.7011e-02, -1.0837e-02, -2.3749e-02,
          -3.3474e-02, -1.9125e-02,  1.5053e-02,  6.4884e-03, -5.9042e-04,
           1.0501e-02, -1.5299e-02, -3.0439e-04,  1.6563e-03, -1.2301e-02,
           5.8770e-02,  5.6771e-03, -2.0859e-02, -7.2198e-03, -1.2947e-02,
           2.6279e-02, -2.5685e-03,  5.5000e-02,  3.5969e-03,  4.0808e-03,
          -1.6978e-02, -4.1970e-03,  1.3250e-02, -4.0225e-03, -7.5401e-03,
           7.4300e-03, -5.4073e-03, -4.7182e-02, -2.2835e-02,  2.7157e-03,
           2.8449e-02,  2.1370e-03,  3.2933e-02,  1.6051e-02, -1.1100e-02,
          -1.3608e-03,  1.3574e-02, -7.2140e-03, -2.6971e-02,  1.2069e-02,
  

In [19]:
checkpoint['model']

OrderedDict([('image_encoder.cls_token',
              tensor([[[-1.2068e-02,  1.3392e-02, -9.6827e-04, -1.7059e-03,  6.0941e-03,
                         5.1860e-03,  2.0641e-02, -2.9634e-02, -1.2990e-02, -4.4133e-04,
                         2.0212e-02, -2.3528e-02,  1.9115e-02,  7.5600e-03,  2.7298e-03,
                        -5.9181e-04, -1.2741e-02,  1.6877e-02, -1.2041e-02, -1.2238e-02,
                         1.8647e-02, -9.5525e-03,  1.7019e-02, -1.0834e-02, -2.3749e-02,
                        -3.3431e-02, -1.9173e-02,  1.5028e-02,  6.4909e-03, -5.9296e-04,
                         1.0503e-02, -1.5282e-02, -3.5274e-04,  1.6318e-03, -1.2321e-02,
                         5.8761e-02,  5.6966e-03, -2.0858e-02, -7.1922e-03, -1.2951e-02,
                         2.6250e-02, -2.5760e-03,  5.4995e-02,  3.6282e-03,  4.0926e-03,
                        -1.6945e-02, -4.1704e-03,  1.3217e-02, -4.0241e-03, -7.5444e-03,
                         7.4438e-03, -5.4145e-03, -4.7206e-02, -2.281

In [16]:
checkpoint['teacher']

OrderedDict([('backbone.cls_token',
              tensor([[[-1.2054e-02,  1.3397e-02, -9.4877e-04, -1.7412e-03,  6.0869e-03,
                         5.1697e-03,  2.0651e-02, -2.9611e-02, -1.3027e-02, -4.3456e-04,
                         2.0252e-02, -2.3503e-02,  1.9098e-02,  7.5740e-03,  2.7332e-03,
                        -5.6026e-04, -1.2754e-02,  1.6864e-02, -1.2023e-02, -1.2214e-02,
                         1.8678e-02, -9.5770e-03,  1.7009e-02, -1.0837e-02, -2.3751e-02,
                        -3.3486e-02, -1.9113e-02,  1.5058e-02,  6.4871e-03, -5.9258e-04,
                         1.0501e-02, -1.5306e-02, -2.9132e-04,  1.6611e-03, -1.2297e-02,
                         5.8773e-02,  5.6699e-03, -2.0860e-02, -7.2273e-03, -1.2946e-02,
                         2.6288e-02, -2.5647e-03,  5.5002e-02,  3.5895e-03,  4.0775e-03,
                        -1.6986e-02, -4.2062e-03,  1.3261e-02, -4.0212e-03, -7.5402e-03,
                         7.4243e-03, -5.4035e-03, -4.7175e-02, -2.2845e-02

In [ ]:
pretrained_weights = "/mnt/c/Users/Moham/Desktop/KAUST/results/checkpoint.pth"
checkpoint_key = "model"
state_dict = torch.load(pretrained_weights, map_location="cpu")
if checkpoint_key is not None and checkpoint_key in state_dict:
    print(f"Take key {checkpoint_key} in provided checkpoint dict")
    state_dict = state_dict[checkpoint_key]
msg = model.load_state_dict(state_dict, strict=False)
print('Pretrained weights found at {} and loaded with msg: {}'.format(pretrained_weights, msg))

In [ ]:
model.discriminative_path.teacher

In [19]:
model.discriminative_path.teacher.backbone

VisionTransformer(
  (patch_embed): PatchEmbed(
    (proj): Conv2d(3, 384, kernel_size=(16, 16), stride=(16, 16))
  )
  (pos_drop): Dropout(p=0.0, inplace=False)
  (blocks): ModuleList(
    (0-11): 12 x Block(
      (norm1): LayerNorm((384,), eps=1e-06, elementwise_affine=True)
      (attn): Attention(
        (qkv): Linear(in_features=384, out_features=1152, bias=True)
        (attn_drop): Dropout(p=0.0, inplace=False)
        (proj): Linear(in_features=384, out_features=384, bias=True)
        (proj_drop): Dropout(p=0.0, inplace=False)
      )
      (drop_path): Identity()
      (norm2): LayerNorm((384,), eps=1e-06, elementwise_affine=True)
      (mlp): Mlp(
        (fc1): Linear(in_features=384, out_features=1536, bias=True)
        (act): GELU(approximate='none')
        (fc2): Linear(in_features=1536, out_features=384, bias=True)
        (drop): Dropout(p=0.0, inplace=False)
      )
    )
  )
  (norm): LayerNorm((384,), eps=1e-06, elementwise_affine=True)
  (head): Identity()
  (f

In [ ]:
for p in model.discriminative_path.teacher.backbone.parameters():
    print(p)

In [18]:
from torchvision import transforms as pth_transforms

train_transform = pth_transforms.Compose([
    pth_transforms.RandomResizedCrop(224),
    pth_transforms.RandomHorizontalFlip(),
    pth_transforms.ToTensor(),
    pth_transforms.Normalize((0.485, 0.456, 0.406), (0.229, 0.224, 0.225)),
])


train_data = torchvision.datasets.ImageFolder("/mnt/e/imagenet-object-localization-challenge/ILSVRC/Data/CLS-LOC/train", transform=train_transform)

data = torch.utils.data.DataLoader(train_data, batch_size=64)

In [19]:
l = 0
for i in data:
    l+=1
    print(l)

1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55


KeyboardInterrupt: 

In [55]:
import os
file_path = os.path.realpath(__file__)

NameError: name '__file__' is not defined

In [52]:
train_data[0][1]

0

In [94]:
from torchvision import datasets
from PIL import Image

class ImageNet(torch.utils.data.Dataset):
    def __init__(self, root, split="train", transform=None, **kwargs):
        self.root = root
        self.transform = transform
        self.split = split

        if split == "train":
            self.data = datasets.ImageFolder(root, transform=transform)
        elif split == "val":
            self.images =  os.listdir(self.root)
            self.image_paths = [os.path.join(self.root, image) for image in self.images]
            self.labels = pd.read_csv(os.path.realpath(__file__) + "/meta/imagenet_val_labels.csv")

    def __len__(self):
        if self.split == "train":
            return self.data.__len__()
        else:
            return len(self.images)

    def get_image_target(self, idx):
        image = Image.open(self.image_paths[idx]).convert("RGB")
        image_name = self.images[idx].split('.')[0]
        label = self.labels[self.labels['ImageId'] == image_name]['PredictionString'].item()
        return image, label

    def __getitem__(self, idx):

        if self.split == "train":
            return self.data[idx][0], self.data[idx][1]
        
        image, target = self.get_image_target(idx)
        
        if self.transform:
            image = self.transform(image)

        return image, target

In [103]:
data = ImageNet(root="/mnt/e/imagenet-object-localization-challenge/ILSVRC/Data/CLS-LOC/train/", split="train")

In [ ]:
import torch
import torch.nn as nn

from timm.models.vision_transformer import PatchEmbed, Block
from vision_transformer import Block

from utils import get_2d_sincos_pos_embed

class GenerativePath(nn.Module):
    def __init__(self, image_encoder, patch_size=16, in_chans=3,
                embed_dim=1024, decoder_embed_dim=512, decoder_depth=8, decoder_num_heads=16,
                mlp_ratio=4, norm_layer=nn.LayerNorm, norm_pix_loss=False):
        super().__init__()

        self.norm_pix_loss = norm_pix_loss
        self.image_encoder = image_encoder
        self.patch_embed = image_encoder.patch_embed
        num_patches = self.image_encoder.patch_embed.num_patches

        self.decoder_embed = nn.Linear(embed_dim, decoder_embed_dim, bias=True)
        self.mask_token = nn.Parameter(torch.zeros(1, 1, decoder_embed_dim))
        self.decoder_pos_embed = nn.Parameter(torch.zeros(1, num_patches + 1, decoder_embed_dim), requires_grad=False)  # fixed sin-cos embedding

        self.decoder_blocks = nn.ModuleList([
            Block(decoder_embed_dim, decoder_num_heads, mlp_ratio, qkv_bias=True, qk_scale=None, norm_layer=norm_layer)
            for i in range(decoder_depth)])

        self.decoder_norm = norm_layer(decoder_embed_dim)
        self.decoder_pred = nn.Linear(decoder_embed_dim, patch_size**2 * in_chans, bias=True) # decoder to patch

    def initialize_deocder_weights(self):
        
        decoder_pos_embed = get_2d_sincos_pos_embed(self.decoder_pos_embed.shape[-1], int(self.patch_embed.num_patches**.5), cls_token=True)
        self.decoder_pos_embed.data.copy_(torch.from_numpy(decoder_pos_embed).float().unsqueeze(0))

        torch.nn.init.normal_(self.mask_token, std=.02)

    def patchify(self, imgs):
        """
        imgs: (N, 3, H, W)
        x: (N, L, patch_size**2 *3)
        """
        print(self.patch_embed.patch_size)
        p = self.patch_embed.patch_size
        assert imgs.shape[2] == imgs.shape[3] and imgs.shape[2] % p == 0

        h = w = imgs.shape[2] // p
        x = imgs.reshape(shape=(imgs.shape[0], 3, h, p, w, p))
        x = torch.einsum('nchpwq->nhwpqc', x)
        x = x.reshape(shape=(imgs.shape[0], h * w, p**2 * 3))
        return x

    def unpatchify(self, x):
        """
        x: (N, L, patch_size**2 *3)
        imgs: (N, 3, H, W)
        """
        p = self.patch_embed.patch_size
        h = w = int(x.shape[1]**.5)
        assert h * w == x.shape[1]
        
        x = x.reshape(shape=(x.shape[0], h, w, p, p, 3))
        x = torch.einsum('nhwpqc->nchpwq', x)
        imgs = x.reshape(shape=(x.shape[0], 3, h * p, h * p))
        return imgs

    def random_masking(self, x, mask_ratio):
        """
        Perform per-sample random masking by per-sample shuffling.
        Per-sample shuffling is done by argsort random noise.
        x: [N, L, D], sequence
        """
        N, L, D = x.shape  # batch, length, dim
        len_keep = int(L * (1 - mask_ratio))
        
        noise = torch.rand(N, L, device=x.device)  # noise in [0, 1]
        
        # sort noise for each sample
        ids_shuffle = torch.argsort(noise, dim=1)  # ascend: small is keep, large is remove
        ids_restore = torch.argsort(ids_shuffle, dim=1)

        # keep the first subset
        ids_keep = ids_shuffle[:, :len_keep]
        x_masked = torch.gather(x, dim=1, index=ids_keep.unsqueeze(-1).repeat(1, 1, D))

        # generate the binary mask: 0 is keep, 1 is remove
        mask = torch.ones([N, L], device=x.device)
        mask[:, :len_keep] = 0
        # unshuffle to get the binary mask
        mask = torch.gather(mask, dim=1, index=ids_restore)

        return x_masked, mask, ids_restore

    def forward_encoder(self, x, mask_ratio):
        # embed patches
        x = self.image_encoder.patch_embed(x)

        # add pos embed w/o cls token
        x = x + self.image_encoder.pos_embed[:, 1:, :]

        # masking: length -> length * mask_ratio
        x, mask, ids_restore = self.random_masking(x, mask_ratio)

        # append cls token
        cls_token = self.image_encoder.cls_token + self.image_encoder.pos_embed[:, :1, :]
        cls_tokens = cls_token.expand(x.shape[0], -1, -1)
        x = torch.cat((cls_tokens, x), dim=1)

        # apply Transformer blocks
        for blk in self.image_encoder.blocks:
            x = blk(x)
        x = self.image_encoder.norm(x)

        return x, mask, ids_restore

    def forward_decoder(self, x, ids_restore):
        # embed tokens
        x = self.decoder_embed(x)

        # append mask tokens to sequence
        mask_tokens = self.mask_token.repeat(x.shape[0], ids_restore.shape[1] + 1 - x.shape[1], 1)
        x_ = torch.cat([x[:, 1:, :], mask_tokens], dim=1)  # no cls token
        x_ = torch.gather(x_, dim=1, index=ids_restore.unsqueeze(-1).repeat(1, 1, x.shape[2]))  # unshuffle
        x = torch.cat([x[:, :1, :], x_], dim=1)  # append cls token

        # add pos embed
        x = x + self.decoder_pos_embed

        # apply Transformer blocks
        for blk in self.decoder_blocks:
            x = blk(x)
        x = self.decoder_norm(x)

        # predictor projection
        x = self.decoder_pred(x)

        # remove cls token
        x = x[:, 1:, :]

        return x

    def forward_loss(self, imgs, pred, mask):
        """
        imgs: [N, 3, H, W]
        pred: [N, L, p*p*3]
        mask: [N, L], 0 is keep, 1 is remove, 
        """
        target = self.patchify(imgs)
        if self.norm_pix_loss:
            mean = target.mean(dim=-1, keepdim=True)
            var = target.var(dim=-1, keepdim=True)
            target = (target - mean) / (var + 1.e-6)**.5

        loss = (pred - target) ** 2
        loss = loss.mean(dim=-1)  # [N, L], mean loss per patch

        loss = (loss * mask).sum() / mask.sum()  # mean loss on removed patches
        return loss

    def forward(self, imgs, mask_ratio=0.75):
        latent, mask, ids_restore = self.forward_encoder(imgs, mask_ratio)
        pred = self.forward_decoder(latent, ids_restore)  # [N, L, p*p*3]
        loss = self.forward_loss(imgs, pred, mask)
        return loss, pred, mask

In [ ]:
s = GenerativePath(image_encoder=model.image_encoder, embed_dim=384).cuda()
r = torch.rand([1, 3, 224, 224]).cuda()

In [ ]:
l, p, m = s(r)

In [ ]:
clip = CLIP_VITL16()

In [ ]:
import torch

In [ ]:
import sys
import os

In [ ]:
a = [f for f in os.scandir("/mnt/d/data/CC3M/cc3m/") if f.is_dir()]

In [ ]:
def save_images_in_folders(folders):
    images_paths = []
    for folder in folders:
        for filename in os.listdir(folder):
            if os.path.isfile(os.path.join(folder, filename)):

In [ ]:
paths = save_images_in_folders(a)

In [ ]:
from PIL import Image

def save_image_captions_in_folders(folders, root):
    images_paths  = []
    captions_path = []
    for folder in folders:
        for filename in os.listdir(folder):
            if os.path.isfile(os.path.join(folder, filename)):
                if ".jpg" in filename or ".png" in filename:
                    images_paths.append(root + os.sep + folder.name + os.sep + filename)
                elif ".txt" in filename:
                    captions_path.append(root + os.sep + folder.name + os.sep + filename)
        break
    return images_paths, captions_path

class CC3M(torch.utils.data.Dataset):
    def __init__(self, root):
        self.root = root
        self.folders =  [f for f in os.scandir(root) if f.is_dir()]
        self.images, self.captions = save_image_captions_in_folders(self.folders, self.root)

        assert len(self.captions) == len(self.images)
        print("Number of images loaded in CC3M are: ", {self.__len__()})

    def __len__(self):
        return len(self.images)

    def get_image_caption_pair(self, idx):
        image = Image.open(self.images[idx])
        
        caption_file = open(self.captions[idx])
        caption = caption_file.read()
        caption_file.close()

        return image, caption


    def __getitem__(self, idx):
        image, caption = self.get_image_caption_pair(idx)
        return image, caption

In [ ]:
a = CC3M(root="/mnt/d/data/CC3M/cc3m")

In [ ]:
i, t = a[0]

In [ ]:
import tarfile

# Open the tar file
tar = tarfile.open(r'D:\data\CC3M\cc3m\00000.tar')

# Loop over each member
for member in tar.getmembers():
    print(member)
    # Extract each file as a file object
    f = tar.extractfile(member)
    if f is not None:
        # Read the contents
        content = f.read()

# Close the tar file
tar.close()
